# Exploratory Data Analysis for repo issues - Jest

In [185]:
from itertools import compress
from ast import literal_eval
import re


import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords, wordnet
from nltk.stem.wordnet import WordNetLemmatizer
from nltk import pos_tag

import matplotlib.pyplot as plt



%matplotlib inline


In [86]:
df_orig = pd.read_csv('data/repo_issue_summary_jest.csv')

Cast columns to appropriate data type

In [87]:
# --- Cast date columns to datetime
cols_date = ['createdAt', 'closedAt', 'firstCommentCreatedAt']
df_orig[cols_date] = df_orig[cols_date].apply(pd.to_datetime)

# --- Cast labels column to list
df_orig['labels'] = df_orig['labels'].apply(literal_eval)

# --- Fill na of the text columns with ''
cols_text = ['title', 'contents']
df_orig[cols_text] = df_orig[cols_text].fillna('')

In [88]:
df_orig.head()

issue_id                                              title  \
0         3  Make global `jest` command line tool like webp...   
1         4  Have a mode to print out a line for each test ...   
2         5  Use jasmine's `toHaveBeenCalled` rather than `...   
3         6                                  Expose a `--help`   
4         7                                    Add a `--watch`   

                                            contents authorLogin  \
0  webpack can be installed globally, but it dele...  sophiebits   
1  More fun that way (instead of just the filename).  sophiebits   
2  13:23  jeffmo: what's the reason behind using ...    chenglou   
3                                                       chenglou   
4                                                       chenglou   

  authorAssociation                 createdAt  closed  \
0       CONTRIBUTOR 2014-05-14 17:17:25+00:00    True   
1       CONTRIBUTOR 2014-05-14 17:26:17+00:00    True   
2       CONTRIBUTOR 2014-05-14 17:26:37+00:00    True   
3       CONTRIBUTOR 2014-05-14 17:56:10+00:00    True   
4       CONTRIBUTOR 2014-05-14 17:57:45+00:00    True   

                   closedAt  closedDuration_days milestone  ...  \
0 2014-05-16 00:15:53+00:00                 1.29       NaN  ...   
1 2015-09-21 23:04:12+00:00               495.23       NaN  ...   
2 2016-04-12 01:45:53+00:00               698.35       NaN  ...   
3 2014-05-15 07:52:07+00:00                 0.58       NaN  ...   
4 2015-10-16 00:18:52+00:00               519.26       NaN  ...   

   label_:boom: Regression  label_Wontfix label_On Hold  label_Has Bounty  \
0                    False          False         False             False   
1                    False          False         False             False   
2                    False          False         False             False   
3                    False          False         False             False   
4                    False          False         False             False   

  label_Coverage label_Bug Report  label_Confirmed  \
0          False            False            False   
1          False            False            False   
2          False            False            False   
3          False            False            False   
4          False            False            False   

   label_Documentation :book:  label_:bug: Bug  label_Needs Triage  
0                       False            False               False  
1                       False            False               False  
2                       False            False               False  
3                       False            False               False  
4                       False            False               False  

[5 rows x 51 columns]

In [89]:
df_orig.shape

(4530, 51)

In [90]:
df_orig['labels'].apply(lambda x: len(x) > 0).sum()

1536

In [91]:
df_orig.groupby(['authorLogin', 'authorAssociation'])['issue_id'].count().sort_values(ascending=False)

authorLogin          authorAssociation
cpojer               CONTRIBUTOR          83
aaronabramov         MEMBER               69
gaearon              MEMBER               43
SimenB               COLLABORATOR         40
thymikee             COLLABORATOR         35
hramos               CONTRIBUTOR          30
kentcdodds           CONTRIBUTOR          25
probablyup           CONTRIBUTOR          21
rogeliog             COLLABORATOR         17
ide                  CONTRIBUTOR          16
hgezim               CONTRIBUTOR          14
Daniel15             MEMBER               14
dandv                CONTRIBUTOR          13
StephanBijzitter     CONTRIBUTOR          13
mjesun               CONTRIBUTOR          13
ColCh                CONTRIBUTOR          13
blainekasten         CONTRIBUTOR          12
binarykitchen        NONE                 12
segrey               NONE                 11
pedrottimark         COLLABORATOR         11
unional              NONE                 10
awei01          

In [92]:
all_cols = df_orig.columns.tolist()

# https://stackoverflow.com/questions/18665873/filtering-a-list-based-on-a-list-of-booleans
cols_labels = list(compress(all_cols, [x.startswith('label_') for x in all_cols]))

In [93]:
df_orig[cols_labels].sum().sort_values(ascending=False)

label_:bug: Bug                             346
label_Help Wanted                           292
label_:rocket: Feature Request              231
label_Needs Triage                          209
label_Needs Repro                           201
label_good first issue                      192
label_Bug Report                            178
label_:rocket: Enhancement                  144
label_Needs More Info :man_shrugging:       132
label_Documentation :book:                  118
label_Confirmed                             118
label_Discussion                             83
label_New API proposal                       42
label_Question                               41
label_Windows                                40
label_:boom: Regression                      37
label_Website                                15
label_Hi-Pri                                 14
label_UX                                     14
label_Wontfix                                 8
label_Infrastructure :hammer_and_wrench:

In [94]:
cols_label_bug = [
    'label_:bug: Bug',
    'label_good first issue',
    'label_Bug Report',
    'label_:boom: Regression',
    'label_Infrastructure :hammer_and_wrench:',
    'label_Upstream Bug',
]

df_label_bugs = df_orig[df_orig[cols_label_bug].sum(axis=1) > 0]


In [95]:
df_label_bugs.groupby(pd.Grouper(key='createdAt', freq='Y'))['issue_id'].count()

createdAt
2014-12-31 00:00:00+00:00      8
2015-12-31 00:00:00+00:00      2
2016-12-31 00:00:00+00:00     43
2017-12-31 00:00:00+00:00    133
2018-12-31 00:00:00+00:00    181
2019-12-31 00:00:00+00:00    368
Freq: A-DEC, Name: issue_id, dtype: int64

In [96]:
df_label_bugs

issue_id                                              title  \
64         102                    Jest does not respect NODE_PATH   
67         106  modulePathIgnorePatterns does not work for nod...   
68         107  Jest does not support jasmine "Runner beforeEach"   
72         112      Add possibility to define module directories.   
73         114               Preprocessor + coffee + source maps?   
79         124   `mockReturnValue` doesn't work with constructors   
81         128  Requiring jsdom throws "Unexpected token ILLEGAL"   
82         129                            Cannot mock htmlparser2   
219        357                      CLI --testPathPattern option?   
333        554    Enable jest mocking to work properly with npm3.   
614       1180         testFileExtensions option fails on Windows   
733       1456  Jest process doesn’t quit after last test comp...   
749       1485     --json parameter should allow saving to a file   
770       1536  `collectCoverageOnlyFrom` documentation is not...   
775       1548   Separate API Reference and Configuration in docs   
805       1600                   Failed tests should re-run first   
806       1603  Idea: command to do a single coverage run in w...   
808       1606          Regex does not work with snapshot testing   
809       1607            Add comment to top of the snapshot file   
813       1612                      Improve snapshot file sorting   
819       1622        Immutable.List is not visible in comparison   
820       1624  moduleNameMapper only works with regexes match...   
823       1633  Snapshot diff displays "null" if diffing a sim...   
824       1634  Too many newlines in --watch mode when no chan...   
835       1652  debugger; and breakpoints don't work with node...   
842       1662                   CLI option to run test by regexp   
859       1694  Jest fails with: "Could not locate the binding...   
869       1726                      Collapse big diffs by default   
877       1739             jest-react-native: Modal is not mocked   
878       1740                 Coverage flag breaks snapshot test   
...        ...                                                ...   
4479      8560       "coverageReporters" : ["json"] doesn't work.   
4480      8561       Code Coverage doesn't fail if coverage is 0%   
4481      8562          Code Coverage doesn't fail with 0% cover.   
4482      8563  Setting "coverageReporters" : ["json"] causes ...   
4484      8567              SNAPSHOTS not generated for Angular 8   
4486      8570  `expect` triggers incompatibility with mocha d...   
4489      8576                        What mean in toBeUndefined?   
4490      8577   No matching version found for @jest/core@^24.8.0   
4492      8580                              confusing source code   
4493      8581  Undefined variable being referenced in custom-...   
4494      8584               Jest encountered an unexpected token   
4495      8585  `import React from 'react'` results in `Object...   
4498      8588          toEqual() on Object with undefined values   
4499      8589                   Universal Acceptance in Facebook   
4500      8590  Mongoose - Timeout - Async callback was not in...   
4501      8594  Jest prints superfluous warning when ran with ...   
4503      8598  Existing inline snapshots get wrong indentatio...   
4504      8599                                    Jest Config Bug   
4506      8601  Different result running single test or test s...   
4510      8605            Error when the project import css files   
4511      8606  Require of path with trailing slash results in...   
4513      8609  Would run too many cases when using --changedS...   
4514      8610    moduleNameMapper does not work with `constants`   
4515      8611  Floating promise side effects after throw or r...   
4516      8613  TypeError: Cannot read property '_cookieJar' o...   
4517      8614  beforeAll is fired even when not in the curren...   
4522

In [97]:
cols_feat_req = [
    'label_:rocket: Feature Request',
    'label_:rocket: Enhancement',
    'label_New API proposal',
]

df_label_feat = df_orig[df_orig[cols_feat_req].sum(axis=1) > 0]


In [98]:
df_label_feat.groupby(pd.Grouper(key='createdAt', freq='Y'))['issue_id'].count()

createdAt
2014-12-31 00:00:00+00:00      7
2015-12-31 00:00:00+00:00      1
2016-12-31 00:00:00+00:00     51
2017-12-31 00:00:00+00:00    125
2018-12-31 00:00:00+00:00    121
2019-12-31 00:00:00+00:00     96
Freq: A-DEC, Name: issue_id, dtype: int64

## Word counts

### Steps:

1. Cleaning to remove irrelevant items, such as HTML tags
2. Normalizing by converting to all lowercase and removing punctuation
3. Splitting text into words or tokens
4. Removing words that are too common, also known as stop words
5. Identifying different parts of speech and named entities
6. Converting words into their dictionary forms, using stemming and lemmatization

In [165]:
issue_text = (df_orig['title'] + ' ' + df_orig['contents']).tolist()

#### 2. Normalization

In [166]:
issue_words = [word_tokenize(x) for x in issue_text]

In [169]:
# Case Normalization

issue_words = [[x.lower() for x in words] for words in issue_words]


In [170]:
# Remove punctuation characters
issue_words = [[x for x in words if len(re.findall(r"^\w+", x)) > 0] for words in issue_words]

In [171]:
issue_words[0]

['make',
 'global',
 'jest',
 'command',
 'line',
 'tool',
 'like',
 'webpack',
 'webpack',
 'can',
 'be',
 'installed',
 'globally',
 'but',
 'it',
 'delegates',
 'to',
 'a',
 'locally-installed',
 'version',
 'if',
 'one',
 'exists',
 'https',
 'l8-l14',
 'perhaps',
 'we',
 'should',
 'consider',
 'the',
 'same',
 'so',
 'that',
 'people',
 'can',
 'use',
 'the',
 'jest',
 'command',
 'easily',
 'instead',
 'of',
 'npm',
 'test']

In [173]:
issue_words = [[w for w in words if w not in stopwords.words("english")] for words in issue_words]

In [174]:
issue_words

[['make',
  'global',
  'jest',
  'command',
  'line',
  'tool',
  'like',
  'webpack',
  'webpack',
  'installed',
  'globally',
  'delegates',
  'locally-installed',
  'version',
  'one',
  'exists',
  'https',
  'l8-l14',
  'perhaps',
  'consider',
  'people',
  'use',
  'jest',
  'command',
  'easily',
  'instead',
  'npm',
  'test'],
 ['mode', 'print', 'line', 'test', 'run', 'fun', 'way', 'instead', 'filename'],
 ['use',
  'jasmine',
  'tohavebeencalled',
  'rather',
  'tobecalled',
  '13:23',
  'jeffmo',
  'reason',
  'behind',
  'using',
  'tobecalled',
  'rather',
  'jasmine',
  'tohavebeencalled',
  '13:24',
  'chenglou',
  'good',
  'question',
  'tobecalled/tohavebeencalled',
  'wondered',
  'layover',
  'jst',
  'really',
  'suspect',
  'leave',
  'support',
  'using',
  'regular',
  'jasmine',
  'spies',
  'wanted'],
 ['expose', 'help'],
 ['add', 'watch'],
 ['test',
  'directory',
  'need',
  '__tests__',
  'feel',
  'like',
  'lot',
  'node',
  'projects',
  'use',
  'lib

In [179]:
# --- Part of speech tagging
pv_tags_words = [pos_tag(words) for words in issue_words]

In [181]:
pv_tags_words[0]

[('make', 'VB'),
 ('global', 'JJ'),
 ('jest', 'NN'),
 ('command', 'NN'),
 ('line', 'NN'),
 ('tool', 'NN'),
 ('like', 'IN'),
 ('webpack', 'NN'),
 ('webpack', 'NN'),
 ('installed', 'VBD'),
 ('globally', 'RB'),
 ('delegates', 'VBZ'),
 ('locally-installed', 'JJ'),
 ('version', 'NN'),
 ('one', 'CD'),
 ('exists', 'VBZ'),
 ('https', 'JJR'),
 ('l8-l14', 'JJ'),
 ('perhaps', 'RB'),
 ('consider', 'VB'),
 ('people', 'NNS'),
 ('use', 'VBP'),
 ('jest', 'JJ'),
 ('command', 'NN'),
 ('easily', 'RB'),
 ('instead', 'RB'),
 ('npm', 'JJ'),
 ('test', 'NN')]

In [182]:
def get_wordnet_pos(tag):
    ''' 
    Get a TreeBank tag from the specified WordNet part of speech name
    Args:
    tag: string. WordNet part of speech name.
    Returns:
    A corresponding TreeBank tag
    '''

    treebank_tag = ''
    # Refer to 
    # https://stackoverflow.com/questions/15586721/wordnet-lemmatization-and-pos-tagging-in-python

    if tag.startswith('J'):
        # Adjective
        treebank_tag = wordnet.ADJ

    elif tag.startswith('V'):
        # Verb
        treebank_tag = wordnet.VERB

    elif tag.startswith('N'):
        # Noun
        treebank_tag = wordnet.NOUN

    elif tag.startswith('R'):
        # Adverb
        treebank_tag = wordnet.ADV

    else:
        # Use Noun as a default output if none of above matches
        treebank_tag = wordnet.NOUN

    return treebank_tag

In [198]:
pv_tags_words[2]

[('use', 'NN'),
 ('jasmine', 'NN'),
 ('tohavebeencalled', 'VBD'),
 ('rather', 'RB'),
 ('tobecalled', 'JJ'),
 ('13:23', 'CD'),
 ('jeffmo', 'NN'),
 ('reason', 'NN'),
 ('behind', 'IN'),
 ('using', 'VBG'),
 ('tobecalled', 'VBD'),
 ('rather', 'RB'),
 ('jasmine', 'NN'),
 ('tohavebeencalled', 'VBD'),
 ('13:24', 'CD'),
 ('chenglou', 'NN'),
 ('good', 'JJ'),
 ('question', 'NN'),
 ('tobecalled/tohavebeencalled', 'VBD'),
 ('wondered', 'VBD'),
 ('layover', 'RB'),
 ('jst', 'JJ'),
 ('really', 'RB'),
 ('suspect', 'JJ'),
 ('leave', 'VBP'),
 ('support', 'NN'),
 ('using', 'VBG'),
 ('regular', 'JJ'),
 ('jasmine', 'NN'),
 ('spies', 'NNS'),
 ('wanted', 'VBD')]

In [209]:
%%time

lemmatizer = WordNetLemmatizer()

# Get current text
final_clean_tokens = []
for cur_pv_tags_words in pv_tags_words:

    cur_clean_tokens = []
    for cur_tag in cur_pv_tags_words:

        cur_text = cur_tag[0]

        # Get a corresponding part of speech that will be used with the lemmatizer
        w_tag = get_wordnet_pos(cur_tag[1])

        # lemmatize the text with pos and append it to clean_tokens
        clean_tok = lemmatizer.lemmatize(cur_text, w_tag)
        cur_clean_tokens.append(clean_tok)
        
    final_clean_tokens.append(cur_clean_tokens)

CPU times: user 1.95 s, sys: 14.7 ms, total: 1.97 s
Wall time: 1.99 s


In [216]:
final_clean_tokens

[['make',
  'global',
  'jest',
  'command',
  'line',
  'tool',
  'like',
  'webpack',
  'webpack',
  'instal',
  'globally',
  'delegate',
  'locally-installed',
  'version',
  'one',
  'exist',
  'https',
  'l8-l14',
  'perhaps',
  'consider',
  'people',
  'use',
  'jest',
  'command',
  'easily',
  'instead',
  'npm',
  'test'],
 ['mode', 'print', 'line', 'test', 'run', 'fun', 'way', 'instead', 'filename'],
 ['use',
  'jasmine',
  'tohavebeencalled',
  'rather',
  'tobecalled',
  '13:23',
  'jeffmo',
  'reason',
  'behind',
  'use',
  'tobecalled',
  'rather',
  'jasmine',
  'tohavebeencalled',
  '13:24',
  'chenglou',
  'good',
  'question',
  'tobecalled/tohavebeencalled',
  'wonder',
  'layover',
  'jst',
  'really',
  'suspect',
  'leave',
  'support',
  'use',
  'regular',
  'jasmine',
  'spy',
  'want'],
 ['expose', 'help'],
 ['add', 'watch'],
 ['test',
  'directory',
  'need',
  '__tests__',
  'feel',
  'like',
  'lot',
  'node',
  'project',
  'use',
  'lib',
  'test',
  '

In [147]:
issue_text

['Make global `jest` command line tool like webpack? webpack can be installed globally, but it delegates to a locally-installed version if one exists:\nhttps://github.com/webpack/webpack/blob/7e08847df59f9bed1854ce660946b285055c73d6/bin/webpack.js#L8-L14\nPerhaps we should consider the same so that people can use the jest command easily instead of npm test.',
 "Have a mode to print out a line for each test that's run More fun that way (instead of just the filename).",
 "Use jasmine's `toHaveBeenCalled` rather than `toBeCalled` 13:23  jeffmo: what's the reason behind using toBeCalled rather than jasmine's toHaveBeenCalled?\n13:24 <•jeffmo> chenglou: good question on toBeCalled/toHaveBeenCalled — I’ve wondered that myself (it’s just layover from jst really). I suspect it was to leave support for using regular jasmine spies if you wanted to",
 'Expose a `--help` ',
 'Add a `--watch` ',
 'Does the test directory need to be __tests__? I feel like a lot of node projects use lib and test as t

In [219]:
final_joined_text = ' '.join([' '.join(words) for words in issue_words])

In [221]:
from wordcloud import WordCloud, STOPWORDS
import matplotlib.pyplot as plt
stopwords = set(STOPWORDS)

ModuleNotFoundError: No module named 'wordcloud'